In [1]:
import pandas as pd
import numpy as np
import torch as t
import plotly.graph_objects as go
import seaborn as sns

In [48]:
# load in residual dataset
residual_data = pd.read_csv(r"/home/tobi/Desktop/Capstone/EnergyDemandForecasting/src/Saved/Datasets/residuals.csv", index_col=0)
residual_data.index = pd.to_datetime(residual_data.index)
residual_data.loc[:,"HourlyPrecipitation"] = residual_data["HourlyPrecipitation"].replace({np.nan:"None"})
display(residual_data)

Energy Demand (MWH)  HourlyDewPointTemperature  \
2018-06-19 05:00:00           929.432931                  14.604973   
2018-06-19 06:00:00           864.640806                  12.510586   
2018-06-19 07:00:00           837.162893                  11.483754   
2018-06-19 08:00:00           844.991945                   9.556321   
2018-06-19 09:00:00           873.515474                  11.710964   
...                                  ...                        ...   
2023-09-01 14:00:00         -1014.998401                 -14.274636   
2023-09-01 15:00:00         -1046.928855                 -12.194302   
2023-09-01 16:00:00         -1017.935878                 -12.151690   
2023-09-01 17:00:00          -977.647300                  -8.147649   
2023-09-01 18:00:00          -933.991323                  -7.166168   

                     HourlyDryBulbTemperature HourlyPrecipitation  \
2018-06-19 05:00:00                 11.413177                None   
2018-06-19 06:00:00                 11.907065                None   
2018-06-19 07:00:00                 12.851306                None   
2018-06-19 08:00:00                 12.327431                None   
2018-06-19 09:00:00                  9.571497                None   
...                                       ...                 ...   
2023-09-01 14:00:00                 -4.430224                None   
2023-09-01 15:00:00                 -5.820376                None   
2023-09-01 16:00:00                 -5.944497                None   
2023-09-01 17:00:00                 -6.950623                None   
2023-09-01 18:00:00                 -8.978128                None   

                     HourlyRelativeHumidity  HourlyStationPressure  \
2018-06-19 05:00:00                7.287526              -0.222017   
2018-06-19 06:00:00                0.328816              -0.222079   
2018-06-19 07:00:00               -4.326148              -0.230828   
2018-06-19 08:00:00               -7.957184              -0.235280   
2018-06-19 09:00:00                2.782851              -0.213443   
...                                     ...                    ...   
2023-09-01 14:00:00              -19.887620               0.332455   
2023-09-01 15:00:00              -14.794391               0.323976   
2023-09-01 16:00:00              -15.271270               0.309880   
2023-09-01 17:00:00               -6.058399               0.311716   
2023-09-01 18:00:00                0.159320               0.311696   

                     HourlyWetBulbTemperature  HourlyWindSpeed  \
2018-06-19 05:00:00                 12.875128         2.934491   
2018-06-19 06:00:00                 11.616646         2.716120   
2018-06-19 07:00:00                 11.124261         0.000000   
2018-06-19 08:00:00                  9.456610         0.000000   
2018-06-19 09:00:00                  9.723082         3.024406   
...                                       ...              ...   
2023-09-01 14:00:00                 -9.872124        -1.918741   
2023-09-01 15:00:00                 -8.577429         1.225462   
2023-09-01 16:00:00                 -9.163044        -4.518683   
2023-09-01 17:00:00                 -7.708875        -4.226650   
2023-09-01 18:00:00                 -7.284336        -3.978355   

                     Energy Price (cents/KWH)     CPI-U  Unemployment Rate  \
2018-06-19 05:00:00                 -0.295352  0.045724          -0.451569   
2018-06-19 06:00:00                 -0.294576  0.044718          -0.451962   
2018-06-19 07:00:00                 -0.293799  0.043558          -0.452508   
2018-06-19 08:00:00                 -0.292928  0.043720          -0.453171   
2018-06-19 09:00:00                 -0.291974  0.045009          -0.453923   
...                                       ...       ...                ...   
2023-09-01 14:00:00                  1.128804  1.023559           0.191135   
2023-09-01 15:00:00                  1.127108  1.023791           0.192188   
202

In [2]:
# load in clean dataset
clean_data = pd.read_csv(r"/home/tobi/Desktop/Capstone/EnergyDemandForecasting/src/Saved/Datasets/clean_training.csv", index_col=0)
clean_data.index = pd.to_datetime(clean_data.index)
clean_data.loc[:,"HourlyPrecipitation"] = clean_data["HourlyPrecipitation"].replace({np.nan:"None"})
display(clean_data)

Energy Demand (MWH)  HourlyDryBulbTemperature  \
2018-06-19 05:00:00               7221.0                      78.0   
2018-06-19 06:00:00               6911.0                      79.0   
2018-06-19 07:00:00               6691.0                      81.0   
2018-06-19 08:00:00               6582.0                      82.0   
2018-06-19 09:00:00               6600.0                      81.0   
...                                  ...                       ...   
2023-09-01 14:00:00               5757.0                      75.0   
2023-09-01 15:00:00               5895.0                      73.0   
2023-09-01 16:00:00               6011.0                      72.0   
2023-09-01 17:00:00               6096.0                      70.0   
2023-09-01 18:00:00               6175.0                      67.0   

                     HourlyDewPointTemperature  HourlyWetBulbTemperature  \
2018-06-19 05:00:00                       72.0                      74.0   
2018-06-19 06:00:00                       70.0                      73.0   
2018-06-19 07:00:00                       69.0                      73.0   
2018-06-19 08:00:00                       67.0                      72.0   
2018-06-19 09:00:00                       69.0                      73.0   
...                                        ...                       ...   
2023-09-01 14:00:00                       47.0                      59.0   
2023-09-01 15:00:00                       49.0                      60.0   
2023-09-01 16:00:00                       49.0                      59.0   
2023-09-01 17:00:00                       53.0                      60.0   
2023-09-01 18:00:00                       54.0                      60.0   

                     HourlyStationPressure HourlyPrecipitation  \
2018-06-19 05:00:00                  29.62                None   
2018-06-19 06:00:00                  29.63                None   
2018-06-19 07:00:00                  29.63                None   
2018-06-19 08:00:00                  29.63                None   
2018-06-19 09:00:00                  29.65                None   
...                                    ...                 ...   
2023-09-01 14:00:00                  30.12                None   
2023-09-01 15:00:00                  30.11                None   
2023-09-01 16:00:00                  30.10                None   
2023-09-01 17:00:00                  30.11                None   
2023-09-01 18:00:00                  30.12                None   

                     HourlyWindSpeed  Energy Price (cents/KWH)  \
2018-06-19 05:00:00         6.000000                     19.28   
2018-06-19 06:00:00         6.000000                     19.28   
2018-06-19 07:00:00         3.565778                     19.28   
2018-06-19 08:00:00         3.814241                     19.28   
2018-06-19 09:00:00         7.000000                     19.28   
...                              ...                       ...   
2023-09-01 14:00:00         3.000000                     23.33   
2023-09-01 15:00:00         6.000000                     23.33   
2023-09-01 16:00:00         0.000000                     23.33   
2023-09-01 17:00:00         0.000000                     23.33   
2023-09-01 18:00:00         0.000000                     23.33   

                     Civilian Noninstitutional Population  \
2018-06-19 05:00:00                             7105823.0   
2018-06-19 06:00:00                             7105823.0   
2018-06-19 07:00:00                             7105823.0   
2018-06-19 08:00:00                             7105823.0   
2018-06-19 09:00:00                             7105823.0   
...                                                   ...   
2023-09-01 14:00:00                             6744964.0   
2023-09-01 15:00:00                             6744964.0   
2023-09-01 16:00:00                             6744964.0   
2023-09-01 17:00:00                             6744964.0   
2023-09-01

In [4]:
input_data = clean_data.copy()
# output_data = clean_data.copy()
# input_data = residual_data.copy()
# output_data = residual_data.copy()

In [8]:
# encode hour of the day, day of the week, and day of the year into a new dataframe
input_time = pd.DataFrame(data={"Hour of Day":input_data.index.hour, "Day of Week":input_data.index.dayofweek, "Day of Year":input_data.index.dayofyear}, index=input_data.index)
display(input_data)
display(input_time)

# should also try doing this without sine and cosine and compare the difference

Energy Demand (MWH)  HourlyDryBulbTemperature  \
2018-06-19 05:00:00               7221.0                      78.0   
2018-06-19 06:00:00               6911.0                      79.0   
2018-06-19 07:00:00               6691.0                      81.0   
2018-06-19 08:00:00               6582.0                      82.0   
2018-06-19 09:00:00               6600.0                      81.0   
...                                  ...                       ...   
2023-09-01 14:00:00               5757.0                      75.0   
2023-09-01 15:00:00               5895.0                      73.0   
2023-09-01 16:00:00               6011.0                      72.0   
2023-09-01 17:00:00               6096.0                      70.0   
2023-09-01 18:00:00               6175.0                      67.0   

                     HourlyDewPointTemperature  HourlyWetBulbTemperature  \
2018-06-19 05:00:00                       72.0                      74.0   
2018-06-19 06:00:00                       70.0                      73.0   
2018-06-19 07:00:00                       69.0                      73.0   
2018-06-19 08:00:00                       67.0                      72.0   
2018-06-19 09:00:00                       69.0                      73.0   
...                                        ...                       ...   
2023-09-01 14:00:00                       47.0                      59.0   
2023-09-01 15:00:00                       49.0                      60.0   
2023-09-01 16:00:00                       49.0                      59.0   
2023-09-01 17:00:00                       53.0                      60.0   
2023-09-01 18:00:00                       54.0                      60.0   

                     HourlyStationPressure  HourlyWindSpeed  \
2018-06-19 05:00:00              29.620001         6.000000   
2018-06-19 06:00:00              29.629999         6.000000   
2018-06-19 07:00:00              29.629999         3.565778   
2018-06-19 08:00:00              29.629999         3.814241   
2018-06-19 09:00:00              29.650000         7.000000   
...                                    ...              ...   
2023-09-01 14:00:00              30.120001         3.000000   
2023-09-01 15:00:00              30.110001         6.000000   
2023-09-01 16:00:00              30.100000         0.000000   
2023-09-01 17:00:00              30.110001         0.000000   
2023-09-01 18:00:00              30.120001         0.000000   

                     Energy Price (cents/KWH)  \
2018-06-19 05:00:00                 19.280001   
2018-06-19 06:00:00                 19.280001   
2018-06-19 07:00:00                 19.280001   
2018-06-19 08:00:00                 19.280001   
2018-06-19 09:00:00                 19.280001   
...                                       ...   
2023-09-01 14:00:00                 23.330000   
2023-09-01 15:00:00                 23.330000   
2023-09-01 16:00:00                 23.330000   
2023-09-01 17:00:00                 23.330000   
2023-09-01 18:00:00                 23.330000   

                     Civilian Noninstitutional Population  \
2018-06-19 05:00:00                             7105823.0   
2018-06-19 06:00:00                             7105823.0   
2018-06-19 07:00:00                             7105823.0   
2018-06-19 08:00:00                             7105823.0   
2018-06-19 09:00:00                             7105823.0   
...                                                   ...   
2023-09-01 14:00:00                             6744964.0   
2023-09-01 15:00:00                             6744964.0   
2023-09-01 16:00:00                             6744964.0   
2023-09-01 17:00:00                             6744964.0   
2023-09-01 18:00:00                             6744964.0   

                     Labor Force Participation       CPI-U  \
2018-06-19 05:00:00                  60.099998  274.170013   
2018-06-19 06:00:00                  60.099998  274.170013   
20

Hour of Day  Day of Week  Day of Year
2018-06-19 05:00:00            5            1          170
2018-06-19 06:00:00            6            1          170
2018-06-19 07:00:00            7            1          170
2018-06-19 08:00:00            8            1          170
2018-06-19 09:00:00            9            1          170
...                          ...          ...          ...
2023-09-01 14:00:00           14            4          244
2023-09-01 15:00:00           15            4          244
2023-09-01 16:00:00           16            4          244
2023-09-01 17:00:00           17            4          244
2023-09-01 18:00:00           18            4          244

[45614 rows x 3 columns]

In [9]:
if t.cuda.is_available():
    device = t.device("cuda")
    print("PyTorch is using:", t.cuda.get_device_name(0))
else:
    print("PyTorch is using CPU")

PyTorch is using: Radeon RX 7900 XTX


Encode Categorical Variables

In [7]:
input_data = pd.get_dummies(input_data, drop_first=True).astype("float32")
# output_data = pd.get_dummies(output_data, drop_first=True).astype("float32")

Normalize features into [0,1]

In [10]:
input_min_vals = np.min(input_data, axis=0)
input_max_vals = np.max(input_data, axis=0)
input_time_min_vals = np.min(input_time, axis=0)
input_time_max_vals = np.max(input_time, axis=0)
# output_min_vals = np.min(output_data, axis=0)
# output_max_vals = np.max(output_data, axis=0)

# Normalize each column to be in the range [0, 1]
input_data = (input_data - input_min_vals) / (input_max_vals - input_min_vals)
input_time = (input_time - input_time_min_vals) / (input_time_max_vals - input_time_min_vals)
# output_data = (output_data - output_min_vals) / (output_max_vals - output_min_vals)

Format using DataLoader

In [13]:
# formatted dataset: (N x B x S x K)
B = 8   # Batch size
S = 168   # Sequence length
K = input_data.shape[1]  # Number of features
steps_ahead = 24

# Reshape data to have dimensions (N x B x S x K)
x = input_data.values
x_time = input_time.values
# y = output_data.values

# Calculate the number of sequences of length S that can be produced
num_sequences = x.shape[0] - (S + steps_ahead)

# Initialize an empty list to store the groups
x_inputs = []
x_time_inputs = []
y_outputs = []

# Iterate over the array to create groups
for i in range(num_sequences):
    input = x[i:i+S]
    time_input = x_time[i:i+S]
    # output = y[i+S]
    output = x[i+S+steps_ahead]
    x_inputs.append(input)
    y_outputs.append(output)
    x_time_inputs.append(time_input)

x_inputs = t.Tensor(np.array(x_inputs))
x_time_inputs = t.Tensor(np.array(x_time_inputs))
y_outputs = t.Tensor(np.array(y_outputs))
display(y_outputs.shape)
display(x_inputs.shape)

validation_size = int(np.floor(x_inputs.shape[0]*0.1))
# define train_loader from 90% of training data
train_dataset = t.utils.data.TensorDataset(x_inputs[:-validation_size], x_time_inputs[:-validation_size], y_outputs[:-validation_size])
train_loader = t.utils.data.DataLoader(train_dataset, batch_size=8, shuffle=False)

# define validation_loader from 10% of training data
validation_dataset = t.utils.data.TensorDataset(x_time_inputs[-validation_size:], y_outputs[-validation_size:])
validation_loader = t.utils.data.DataLoader(validation_dataset, batch_size=1, shuffle=False)
initial_validation_time = input_time.index[-validation_size]

torch.Size([45422, 13])

torch.Size([45422, 168, 13])

In [55]:
for x_input, time_input, output in train_loader:
    print(x_input.shape)
    print(time_input.shape)
    print(output.shape)
    break

# Test formatting
# y_index = np.random.randint(y.shape[0]*y.shape[1]-1)
y_index = np.random.randint(y_outputs.shape[0])
y_sample_index = y_index//B
y_batch_index = y_index%B

x_index = y_index + 1
x_sample_index = x_index//B
x_batch_index = x_index%B

display(train_loader.dataset[x_index][0][-1].numpy() * (input_max_vals-input_min_vals) + input_min_vals)
display(train_loader.dataset[y_index][2].numpy() * (input_max_vals-input_min_vals) + input_min_vals)

torch.Size([8, 168, 20])
torch.Size([8, 168, 3])
torch.Size([8, 20])


Energy Demand (MWH)                     -544.287354
HourlyDewPointTemperature                 -8.091679
HourlyDryBulbTemperature                  -6.831139
HourlyRelativeHumidity                    -7.527214
HourlyStationPressure                      0.181642
HourlyWetBulbTemperature                  -7.092628
HourlyWindSpeed                            0.000000
Energy Price (cents/KWH)                   0.186056
CPI-U                                      0.002073
Unemployment Rate                          0.127016
Unemployment Level                      3926.546875
Employment Level                        6446.406250
Labor Force Level                       6696.718750
Employment Population Ratio                0.095750
Labor Force Participation                  0.070424
Civilian Noninstitutional Population    -199.582031
Payroll Employment                        -2.708679
HourlyPrecipitation_Light Rain             0.000000
HourlyPrecipitation_Medium Rain            0.000000
HourlyPrecip

Energy Demand (MWH)                     -544.287354
HourlyDewPointTemperature                 -8.091679
HourlyDryBulbTemperature                  -6.831139
HourlyRelativeHumidity                    -7.527214
HourlyStationPressure                      0.181642
HourlyWetBulbTemperature                  -7.092628
HourlyWindSpeed                            0.000000
Energy Price (cents/KWH)                   0.186056
CPI-U                                      0.002073
Unemployment Rate                          0.127016
Unemployment Level                      3926.546875
Employment Level                        6446.406250
Labor Force Level                       6696.718750
Employment Population Ratio                0.095750
Labor Force Participation                  0.070424
Civilian Noninstitutional Population    -199.582031
Payroll Employment                        -2.708679
HourlyPrecipitation_Light Rain             0.000000
HourlyPrecipitation_Medium Rain            0.000000
HourlyPrecip

In [56]:
import numpy as np

class LSTM(t.nn.Module):
    def __init__(self, input_size, hidden_size, num_layers, output_size, dropout:float = 0):
        super(LSTM, self).__init__()
        self.hidden_size = hidden_size
        self.num_layers = num_layers
        self.lstm = t.nn.LSTM(input_size, hidden_size, num_layers, batch_first=True)
        self.dropout = t.nn.Dropout(dropout)
        self.fc = t.nn.Sequential(
            # t.nn.Linear(hidden_size, hidden_size),
            t.nn.Linear(hidden_size, output_size),
            t.nn.Softplus() 
        ) 
        self.c0 = None
        self.h0 = None

    def forward(self, x_observed, x_time, save_cell_state:bool=False, bayesian_predict:bool=False):
        x = t.cat([x_observed, x_time], dim=-1)
        device = next(self.parameters()).device
        if save_cell_state: # Use previous hidden state and cell state
            if self.c0 is None: # no previous states so need to initialize them
                self.h0 = t.zeros(self.num_layers, x.size(0), self.hidden_size).to(x.device)
                self.c0 = t.zeros(self.num_layers, x.size(0), self.hidden_size).to(x.device)
            h0 = self.c0
            c0 = self.h0
        else: # Initialize hidden state and cell state
            h0 = t.zeros(self.num_layers, x.size(0), self.hidden_size, device=device)
            c0 = t.zeros(self.num_layers, x.size(0), self.hidden_size, device=device)


        # Forward propagate LSTM
        out, (h0, c0) = self.lstm(x, (h0, c0))

        # Decode the hidden state of the last time step
        if self.eval or bayesian_predict:
            out = self.dropout(out)
        out = self.fc(out[:, -1, :])
        return out
    
    def predict_future(self, initial_input, input_order): pass


# Example usage:
display(train_loader.dataset[0][0].shape)
input_size = train_loader.dataset[0][0].shape[-1] + train_loader.dataset[0][1].shape[-1]
hidden_size = 32  # Number of LSTM units (hidden size)
num_layers = 1  # Number of LSTM layers
output_size = train_loader.dataset[0][2].shape[-1]
seq_length = S  # Length of input sequence (assuming hourly data)

# Forward pass
model = LSTM(input_size, hidden_size, num_layers, output_size)
output = model(train_loader.dataset[0][0][None,:,:], train_loader.dataset[0][1][None,:,:])
print("Output shape:", output.shape)

torch.Size([168, 20])

Output shape: torch.Size([1, 20])


Train

In [57]:
# set device
device = "cuda"
# device = "cpu"
# Initialize the LSTM model
model = LSTM(input_size, hidden_size, num_layers, output_size).to(device=device)

# pull out last 10% of data to use for early stopping validation

# define optimizer
criterion = t.nn.MSELoss(reduction="none")
optimizer = t.optim.Adam(model.parameters(), lr=0.001, weight_decay=0)
# x_device = t.Tensor(x).to(device=device)
# y_device = t.Tensor(y).to(device=device)
weights = t.Tensor([1]+[0.1]*(train_loader.dataset[0][2].shape[-1]-1)).to(device=device)

for epoch in range(10):
    # for b in range(x.shape[0]):
    losses = []
    for b, (inputs, time_inputs, targets) in enumerate(train_loader):
        inputs = inputs.to(device=device)
        time_inputs = time_inputs.to(device=device)
        targets = targets.to(device=device)
        # outputs = model(x_device[b])
        outputs = model(inputs, time_inputs)
        optimizer.zero_grad()
        loss = criterion(targets, outputs) * 1000
        
        loss = loss * weights[None,:]
        loss = t.mean(loss)
        # print(loss.item())
        losses.append(loss.item())
        # loss = criterion(y_gpu[b], outputs)
        loss.backward()
        # Print gradients of model parameters
        if (epoch % 25 == 0) & (b == 0):
            for name, param in model.named_parameters():
                if param.grad is not None:
                    print(f"Gradient of {name}:")
                    print(param.grad)
                    print(param)
        optimizer.step()
        # print("Batch {}, Loss: {:.2f}".format(b+1, loss.item()))
    # print("NEW EPOCH\n\n\n")
    # if epoch == 1: break
    losses = np.mean(losses)
    print("Epoch {}, Loss: {}".format(epoch+1, losses.item()))

Gradient of lstm.weight_ih_l0:
tensor([[ 0.0258,  0.0653,  0.0679,  ...,  0.0433,  0.0254,  0.0737],
        [-0.0175, -0.0407, -0.0425,  ..., -0.0249, -0.0159, -0.0466],
        [-0.0016, -0.0032, -0.0030,  ..., -0.0008, -0.0013, -0.0037],
        ...,
        [ 0.0117,  0.0356,  0.0372,  ...,  0.0295,  0.0135,  0.0389],
        [-0.0041, -0.0105, -0.0111,  ..., -0.0083, -0.0039, -0.0118],
        [-0.0305, -0.0857, -0.0889,  ..., -0.0623, -0.0330, -0.0950]],
       device='cuda:0')
Parameter containing:
tensor([[ 0.0515,  0.0108,  0.0225,  ..., -0.0529, -0.0429, -0.0569],
        [ 0.0037, -0.1458, -0.0279,  ...,  0.0356,  0.0242, -0.1760],
        [-0.1318,  0.0020,  0.0963,  ...,  0.0298, -0.1420, -0.0323],
        ...,
        [-0.1149, -0.0968, -0.0358,  ..., -0.1648, -0.1174, -0.0836],
        [-0.0062, -0.0278,  0.0214,  ..., -0.1762,  0.0297,  0.0541],
        [ 0.0072, -0.1272,  0.0731,  ...,  0.0049,  0.0319,  0.0237]],
       device='cuda:0', requires_grad=True)
Gradient of

Evaluate on training data. Initially, we want the model to be able to overfit the training data.

In [60]:
model = model.to(device=device)
predictions = []
with t.no_grad():
    losses = []
    time_inputs = t.cat([data[1] for data in train_loader])
    targets = t.cat([data[2] for data in train_loader])
    inputs = train_loader.dataset[0][0][None,:,:].to(device=device)
    for i in range(len(time_inputs)):
        # inputs = inputs.to(device=device)
        # time_inputs = time_inputs.to(device=device)
        time_input = time_inputs[i][None,:,:].to(device=device)
        target = targets[i][None,:].to(device=device)
        # print(inputs.shape)
        # print(time_input.shape)
        # print(target.shape)
        output = model(inputs, time_input)
        # print(output.shape)
        # print(output.cpu().numpy().shape)
        # break
        predictions.append(output.cpu().numpy())
        loss = criterion(target, output) * 1000
        
        loss = loss * weights[None,:]
        loss = t.mean(loss)
        losses.append(loss.item())

        # display(inputs)
        # display(output)
        # display(target)

        inputs = inputs[:,1:]

        inputs = t.cat([inputs, output[:,None,:]], dim=1)
        # display(inputs)
        # display(inputs.shape)
        # break

    losses = np.mean(losses)
    predictions = np.concatenate(predictions, axis=0)
    print("Training Loss: {}".format(losses.item()))

Training Loss: 5.2005303418057505


In [61]:
# plot training data. Trying to troubleshoot validation.
display(predictions.shape)
dependent_variable = "Energy Demand (MWH)"
prediction_data = (predictions[:,0] * (output_max_vals[dependent_variable]-output_min_vals[dependent_variable]) + output_min_vals[dependent_variable]).flatten()
display(prediction_data)

train_data = t.cat([batch[2] for batch in train_loader])
display(train_data.shape)
train_data = (train_data[:,0].cpu().numpy() * (output_max_vals[dependent_variable]-output_min_vals[dependent_variable]) + output_min_vals[dependent_variable]).flatten()
display(train_data)

trace1 = go.Scatter(x = np.array(range(0, train_data.shape[0])), y=train_data, mode="lines")
trace2 = go.Scatter(x = np.array(range(0, prediction_data.shape[0])), y=prediction_data, mode="lines")

fig = go.Figure([trace1, trace2])
fig.show()

(40902, 20)

array([-765.6432  , -549.2162  , -342.74646 , ...,   29.648193,
         24.794922,   16.131348], dtype=float32)

torch.Size([40902, 20])

array([-1086.2274  , -1173.4557  , -1218.3677  , ...,   -61.098877,
        -101.51135 ,  -203.47058 ], dtype=float32)

Evaluate on validation data.

In [62]:
model = model.to(device=device)
predictions = []
with t.no_grad():
    # validation
    losses = []
    inputs = train_loader.dataset[-1][0][None,:,:].to(device=device)
    for b, (time_inputs, targets) in enumerate(validation_loader):
        # print(train_loader.dataset[-1][0].shape)
        # print(inputs.shape)
        time_inputs = time_inputs.to(device=device)
        targets = targets.to(device=device)
        # print(inputs.device)
        # print(time_inputs.device)
        # print(model.device)
        output = model(inputs, time_inputs)
        predictions.append(output.cpu().numpy())
        loss = criterion(targets, output) * 1000
        
        loss = loss * weights[None,:]
        loss = t.mean(loss)
        losses.append(loss.item())

        inputs = inputs[:,1:]
        # print(inputs.shape)
        # print(output * (output_max_vals.iloc[0]-output_min_vals.iloc[0]) + output_min_vals.iloc[0])
        # print(output[:,None,:].shape)
        # print(output.device)
        output = output
        inputs = t.cat([inputs, output[:,None,:]], dim=1)
        # print(inputs.shape)

    losses = np.mean(losses)
    predictions = np.array(predictions)
    print("Epoch {}, Loss: {}".format(epoch+1, losses.item()))

Epoch 10, Loss: 4.866257402347401


In [63]:
# tensor_dataset = torch.cat([batch for batch in data_loader])
display(predictions.shape)
dependent_variable = "Energy Demand (MWH)"
prediction_data = (predictions[:,:,0] * (output_max_vals[dependent_variable]-output_min_vals[dependent_variable]) + output_min_vals[dependent_variable]).flatten()
display(prediction_data)

val_data = t.cat([batch[1] for batch in validation_loader])
val_data = (val_data[:,0].cpu().numpy() * (output_max_vals[dependent_variable]-output_min_vals[dependent_variable]) + output_min_vals[dependent_variable]).flatten()
display(val_data)

trace1 = go.Scatter(x = np.array(range(0, val_data.shape[0])), y=val_data, mode="lines")
trace2 = go.Scatter(x = np.array(range(0, prediction_data.shape[0])), y=prediction_data, mode="lines")

fig = go.Figure([trace1, trace2])
fig.show()

(4544, 1, 20)

array([-132.005  , -123.46057, -117.62439, ...,  629.54517,  678.41675,
        727.27124], dtype=float32)

array([ -264.01184,  -201.4668 ,  -192.3208 , ..., -1017.93585,
        -977.6473 ,  -933.99133], dtype=float32)

Define validation function

In [85]:
# initial_input = train_loader.dataset[-1][0]
# display(train_loader.dataset[-1][1].numpy().shape)
# validation_time = train_loader.dataset[-1][1][-1].numpy() * (input_time_max_vals-input_time_min_vals) + input_time_min_vals

display(initial_validation_time)

# Define the number of periods (hours)
N = len(validation_loader)  # 7 days worth of hourly data

# Generate hourly timestamps
validation_time = [initial_validation_time + pd.Timedelta(hours=i) for i in range(N)]
validation_time = pd.DatetimeIndex(validation_time)
validation_time = pd.DataFrame(data={"Hour of Day":validation_time.hour, "Day of Week":validation_time.dayofweek, "Day of Year":validation_time.dayofyear})

Timestamp('2023-01-31 04:00:00')

DatetimeIndex(['2023-01-31 04:00:00', '2023-01-31 05:00:00',
               '2023-01-31 06:00:00', '2023-01-31 07:00:00',
               '2023-01-31 08:00:00', '2023-01-31 09:00:00',
               '2023-01-31 10:00:00', '2023-01-31 11:00:00',
               '2023-01-31 12:00:00', '2023-01-31 13:00:00',
               ...
               '2023-08-05 09:00:00', '2023-08-05 10:00:00',
               '2023-08-05 11:00:00', '2023-08-05 12:00:00',
               '2023-08-05 13:00:00', '2023-08-05 14:00:00',
               '2023-08-05 15:00:00', '2023-08-05 16:00:00',
               '2023-08-05 17:00:00', '2023-08-05 18:00:00'],
              dtype='datetime64[ns]', length=4479, freq=None)

Hour of Day  Day of Week  Day of Year
0               4            1           31
1               5            1           31
2               6            1           31
3               7            1           31
4               8            1           31
...           ...          ...          ...
4474           14            5          217
4475           15            5          217
4476           16            5          217
4477           17            5          217
4478           18            5          217

[4479 rows x 3 columns]

4479

Rolling Cross Validation